In [72]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [73]:
import os
import sys
from pathlib import Path

# check if workding_dir is in local variables
if 'workding_dir' not in locals():
    workding_dir = str(Path.cwd().parent)

os.chdir(workding_dir)
sys.path.append(workding_dir)
print("workding dir:", workding_dir)

workding dir: /Users/inflaton/code/engd/papers/rapget-translation


In [74]:
from dotenv import find_dotenv, load_dotenv

found_dotenv = find_dotenv(".env")

if len(found_dotenv) == 0:
    found_dotenv = find_dotenv(".env.example")
print(f"loading env vars from: {found_dotenv}")
load_dotenv(found_dotenv, override=True)

loading env vars from: /Users/inflaton/code/engd/papers/rapget-translation/.env


True

In [75]:
import os

model_name = os.getenv("MODEL_NAME")
adapter_name_or_path = os.getenv("ADAPTER_NAME_OR_PATH")
load_in_4bit = os.getenv("LOAD_IN_4BIT") == "true"
data_path = os.getenv("DATA_PATH")
results_path = os.getenv("RESULTS_PATH")
use_english_datasets = os.getenv("USE_ENGLISH_DATASETS") == "true"

print(model_name, adapter_name_or_path, load_in_4bit, data_path, results_path)

Qwen/Qwen2-7B-Instruct None False datasets/mac/mac.tsv results/mac-results.csv


In [76]:
%%time
os.environ["TOKENIZERS_PARALLELISM"] = "true"

!python --version
!pip show torch transformers

Python 3.11.9
Name: torch
Version: 2.4.0
Summary: Tensors and Dynamic neural networks in Python with strong GPU acceleration
Home-page: https://pytorch.org/
Author: PyTorch Team
Author-email: packages@pytorch.org
License: BSD-3
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, fsspec, jinja2, networkx, sympy, typing-extensions
Required-by: accelerate, peft, torchaudio, torchvision
---
Name: transformers
Version: 4.43.3
Summary: State-of-the-art Machine Learning for JAX, PyTorch and TensorFlow
Home-page: https://github.com/huggingface/transformers
Author: The Hugging Face team (past and future) with the help of all our contributors (https://github.com/huggingface/transformers/graphs/contributors)
Author-email: transformers@huggingface.co
License: Apache 2.0 License
Location: /Users/inflaton/anaconda3/envs/rapget/lib/python3.11/site-packages
Requires: filelock, huggingface-hub, numpy, packaging, pyyaml, regex, requests, safetensors, tokenize

In [77]:
from llm_toolkit.llm_utils import *
from llm_toolkit.translation_utils import *

device = check_gpu()

MPS is available


In [78]:
import pandas as pd

df = pd.read_csv(results_path)
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1133 entries, 0 to 1132
Data columns (total 20 columns):
 #   Column                                    Non-Null Count  Dtype 
---  ------                                    --------------  ----- 
 0   chinese                                   1133 non-null   object
 1   english                                   1133 non-null   object
 2   Qwen/Qwen2-7B-Instruct/rpp-1.00           1133 non-null   object
 3   Qwen/Qwen2-7B-Instruct/rpp-1.02           1133 non-null   object
 4   Qwen/Qwen2-7B-Instruct/rpp-1.04           1133 non-null   object
 5   Qwen/Qwen2-7B-Instruct/rpp-1.06           1133 non-null   object
 6   Qwen/Qwen2-7B-Instruct/rpp-1.08           1133 non-null   object
 7   Qwen/Qwen2-7B-Instruct/rpp-1.10           1133 non-null   object
 8   Qwen/Qwen2-7B-Instruct/rpp-1.12           1133 non-null   object
 9   Qwen/Qwen2-7B-Instruct/rpp-1.14           1133 non-null   object
 10  Qwen/Qwen2-7B-Instruct/rpp-1.16           1133 n

In [79]:
metrics_df = get_metrics(df)
metrics_df

Qwen/Qwen2-7B-Instruct/rpp-1.00: {'meteor': 0.37372392521659187, 'bleu_scores': {'bleu': 0.11236357019695803, 'precisions': [0.42194734753274243, 0.15166821289901386, 0.07014658562745799, 0.035509352410760864], 'brevity_penalty': 1.0, 'length_ratio': 1.0015236833388539, 'translation_length': 30236, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.42297796931661225, 'rouge2': 0.17403983204578213, 'rougeL': 0.3658856686382874, 'rougeLsum': 0.3659204687398736}, 'accuracy': 0.00264783759929391, 'correct_ids': [240, 364, 659]}
Qwen/Qwen2-7B-Instruct/rpp-1.02: {'meteor': 0.37190869873532223, 'bleu_scores': {'bleu': 0.1100390286367209, 'precisions': [0.4184028352820377, 0.1497005988023952, 0.06846911369740376, 0.03418803418803419], 'brevity_penalty': 1.0, 'length_ratio': 1.0000331235508446, 'translation_length': 30191, 'reference_length': 30190}, 'rouge_scores': {'rouge1': 0.4195845948970141, 'rouge2': 0.17186391930180184, 'rougeL': 0.361164889670589, 'rougeLsum': 0.36115367651131036}

model   rpp    meteor    bleu_1   rouge_l  ews_score  \
0        Qwen2-7B-Instruct  1.00  0.373724  0.112364  0.365886   0.000000   
1        Qwen2-7B-Instruct  1.02  0.371909  0.110039  0.361165   0.000000   
2        Qwen2-7B-Instruct  1.04  0.374066  0.109569  0.361896   0.000000   
3        Qwen2-7B-Instruct  1.06  0.374308  0.109368  0.361424   0.000000   
4        Qwen2-7B-Instruct  1.08  0.373892  0.112526  0.361545   0.000000   
5        Qwen2-7B-Instruct  1.10  0.370259  0.107103  0.358990   0.000000   
6        Qwen2-7B-Instruct  1.12  0.370576  0.102582  0.357009   0.000000   
7        Qwen2-7B-Instruct  1.14  0.364111  0.099032  0.352458   0.000000   
8        Qwen2-7B-Instruct  1.16  0.363139  0.095287  0.349748   0.000000   
9        Qwen2-7B-Instruct  1.18  0.362194  0.094761  0.346995   0.000000   
10       Qwen2-7B-Instruct  1.20  0.353817  0.089690  0.342185   0.000000   
11       Qwen2-7B-Instruct  1.22  0.351813  0.084682  0.337275   0.000000   
12       Qwen2-7B-Instruct  1.24  0.347819  0.080593  0.335893   0.000000   
13       Qwen2-7B-Instruct  1.26  0.343773  0.073788  0.328662   0.000000   
14       Qwen2-7B-Instruct  1.28  0.340176  0.072698  0.326574   0.000000   
15       Qwen2-7B-Instruct  1.30  0.335370  0.058301  0.320998   0.004413   
16  internlm2_5-7b-chat-1m  1.00  0.371530  0.099209  0.363271   0.000000   
17  internlm2_5-7b-chat-1m  1.02  0.352901  0.086979  0.340282   0.000000   

    repetition_score  total_repetitions  
0           0.000000           0.000000  
1           0.000000           0.000000  
2           0.000000           0.000000  
3           0.000000           0.000000  
4           0.000000           0.000000  
5           0.000000           0.000000  
6           0.000000           0.000000  
7           0.000000           0.000000  
8           0.000000           0.000000  
9           0.000000           0.000000  
10          0.000000           0.000000  
11          0.000000           0.000000  
12          0.000000           0.000000  
13          0.000000           0.000000  
14          0.000000           0.000000  
15          0.004413           0.004413  
16          0.000000           0.000000  
17          0.000000           0.000000

In [82]:
col = "Qwen/Qwen2-7B-Instruct/rpp-1.30"
df[["ews_score", "repetition_score", "total_repetitions"]] = df[col].apply(
    detect_scores
)

In [88]:
rows = df.query("ews_score > 0")
rows

chinese                                            english  \
905  顾炎武举起酒杯，高声吟道：  Gu Yanwu raised his wine-cup and, in ringing t...   

                     Qwen/Qwen2-7B-Instruct/rpp-1.00  \
905  Ku Yanyu lifted his wine cup and recited aloud:   

                      Qwen/Qwen2-7B-Instruct/rpp-1.02  \
905  Ku Yanyu lifted his wine cup and recited loudly:   

                Qwen/Qwen2-7B-Instruct/rpp-1.04  \
905  Ku Yanyu raised his cup and recited aloud:   

                     Qwen/Qwen2-7B-Instruct/rpp-1.06  \
905  Ku Yanyu raised his wine cup and recited aloud:   

                      Qwen/Qwen2-7B-Instruct/rpp-1.08  \
905  Ku Yanyu lifted his wine cup and recited loudly:   

                     Qwen/Qwen2-7B-Instruct/rpp-1.10  \
905  Ku Yanyu raised his wine cup and recited aloud:   

                       Qwen/Qwen2-7B-Instruct/rpp-1.12  \
905  Ku Yanyu raised his cup and recited loudly:\n\...   

                       Qwen/Qwen2-7B-Instruct/rpp-1.14  ...  \
905  Ku Yanyu lifted his wine cup and recited loudl...  ...   

                       Qwen/Qwen2-7B-Instruct/rpp-1.22  \
905  Ku Yanyun raised his cup and recited loudly:\n...   

                       Qwen/Qwen2-7B-Instruct/rpp-1.24  \
905  Ku Yanyuan raised his cup and recited loudly:\...   

                 Qwen/Qwen2-7B-Instruct/rpp-1.26  \
905  Ku Yanyun raised his cup and recited aloud:   

                 Qwen/Qwen2-7B-Instruct/rpp-1.28  \
905  Ku Yanyun raised his cup and recited aloud:   

                       Qwen/Qwen2-7B-Instruct/rpp-1.30  \
905  Ku Yanyuan raised his cup and recited loudly:\...   

             internlm/internlm2_5-7b-chat-1m/rpp-1.00  \
905  Gu Yanwu raised his wine cup and recited loudly:   

             internlm/internlm2_5-7b-chat-1m/rpp-1.02 ews_score  \
905  Gu Yanwu raised his wine cup and recited loudly:         5   

    repetition_score total_repetitions  
905                0                 5  

[1 rows x 23 columns]

In [92]:
row = rows.iloc[0]

In [93]:
print(row["chinese"])

顾炎武举起酒杯，高声吟道：


In [94]:
print(row["english"])

Gu Yanwu raised his wine-cup and, in ringing tones, recited the following couplet:


In [97]:
print(row["Qwen/Qwen2-7B-Instruct/rpp-1.30"])

Ku Yanyuan raised his cup and recited loudly:

"Under Heaven's vast expanse,
The world is full of myriad paths;
Yet every step I take leads me back home.

I've sought solace amidst mountains high,
And found tranquility by rivers wide;  
But my heart yearns for that familiar place."

He then took a deep sip from his wine goblet before continuing with another verse:
 
"In this mortal coil we wander on,
Seeking truth where'er our feet have gone;
Our souls forever roam like birds free,

Yearning always after what was lost or missed,
In dreams as well as waking hours past."
   
With each word echoing through the hallways filled with ancient wisdom, Ku’s verses seemed to carry echoes beyond their literal meaning—touching upon themes deeply rooted within human experience: longing, memory, identity, and perhaps most importantly—the universal quest for belongingness amid life’s transient nature. 

His poetic outpourings resonated not just because they captured moments specific to one man but du